In [ ]:
!pip install transformers

In [ ]:
from google.colab import drive
drive.mount("/content/drive/")

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


In [ ]:
import pandas as pd
import matplotlib.pyplot as plt
import torch
import torch.nn as nn
import pandas as pd
import numpy as np
import shutil
import sys
import os

In [ ]:
save_path = "/content/drive/MyDrive/datasets/multi-label/weights.txt"
load_path = save_path
save_dir = "/content/drive/MyDrive/datasets/multi-label"

In [ ]:
train_path = "/content/drive/MyDrive/datasets/data/train_.csv"
test_path = "/content/drive/MyDrive/datasets/data/test_.csv"

In [ ]:
train_df = pd.read_csv(train_path)
train_df['UnrelevantText'] = 0
train_df = train_df.head(len(train_df)//2)
test_df = pd.read_csv(test_path)
test_df['UnrelevantText'] = 0
test_df = test_df.head(len(train_df)//2)

In [ ]:
print(train_df.shape)

(10486, 10)


In [ ]:
train_df.head()

ID                                              TITLE  \
0   1        Reconstructing Subject-Specific Effect Maps   
1   2                 Rotation Invariance Neural Network   
2   3  Spherical polyharmonics and Poisson kernels fo...   
3   4  A finite element approximation for the stochas...   
4   5  Comparative study of Discrete Wavelet Transfor...   

                                            ABSTRACT  Computer Science  \
0    Predictive models allow subject-specific inf...                 1   
1    Rotation invariance and translation invarian...                 1   
2    We introduce and develop the notion of spher...                 0   
3    The stochastic Landau--Lifshitz--Gilbert (LL...                 0   
4    Fourier-transform infra-red (FTIR) spectra o...                 1   

   Physics  Mathematics  Statistics  Quantitative Biology  \
0        0            0           0                     0   
1        0            0           0                     0   
2        0            1           0                     0   
3        0            1           0                     0   
4        0            0           1                     0   

   Quantitative Finance  UnrelevantText  
0                     0               0  
1                     0               0  
2                     0               0  
3                     0               0  
4                     0               0

In [ ]:
train_df.tail()

ID                                              TITLE  \
10481  10482  A quick guide for student-driven community gen...   
10482  10483  Copycat CNN: Stealing Knowledge by Persuading ...   
10483  10484  Medoids in almost linear time via multi-armed ...   
10484  10485  Early stopping for statistical inverse problem...   
10485  10486  Algorithmic Theory of ODEs and Sampling from W...   

                                                ABSTRACT  Computer Science  \
10481    High quality gene models are necessary to ex...                 0   
10482    In the past few years, Convolutional Neural ...                 0   
10483    Computing the medoid of a large number of po...                 1   
10484    We consider truncated SVD (or spectral cut-o...                 0   
10485    Sampling logconcave functions arising in sta...                 1   

       Physics  Mathematics  Statistics  Quantitative Biology  \
10481        0            0           0                     1   
10482        0            0           1                     0   
10483        0            0           1                     0   
10484        0            1           1                     0   
10485        0            0           0                     0   

       Quantitative Finance  UnrelevantText  
10481                     0               0  
10482                     0               0  
10483                     0               0  
10484                     0               0  
10485                     0               0

In [ ]:
# combining 'title' and 'abstract' column to| get more context
train_df['CONTEXT'] = train_df['TITLE'] + ". " + train_df['ABSTRACT']

In [ ]:
# dropping useless features/columns
train_df.drop(labels=['TITLE', 'ABSTRACT', 'ID'], axis=1, inplace=True)

In [ ]:
train_df.columns

Index(['Computer Science', 'Physics', 'Mathematics', 'Statistics',
       'Quantitative Biology', 'Quantitative Finance', 'UnrelevantText',
       'CONTEXT'],
      dtype='object')

In [ ]:
# rearranging columns
#train_df = train_df[['Частный', 'Государственный', 'Муниципальный', 'Смешанный', 'Стартап', 'Малый', 'Средний', 'Крупный', 'Локальный', 'Региональный', 'Международный', 'Физ.Лица', 'Юр.Лица', 'UnrelevantText', 'CONTEXT']]
train_df = train_df[['Computer Science', 'Physics', 'Mathematics', 'Statistics', 'Quantitative Biology', 'Quantitative Finance', 'UnrelevantText', 'CONTEXT']]

In [ ]:
train_df.head()

Computer Science  Physics  Mathematics  Statistics  Quantitative Biology  \
0                 1        0            0           0                     0   
1                 1        0            0           0                     0   
2                 0        0            1           0                     0   
3                 0        0            1           0                     0   
4                 1        0            0           1                     0   

   Quantitative Finance  UnrelevantText  \
0                     0               0   
1                     0               0   
2                     0               0   
3                     0               0   
4                     0               0   

                                             CONTEXT  
0  Reconstructing Subject-Specific Effect Maps.  ...  
1  Rotation Invariance Neural Network.   Rotation...  
2  Spherical polyharmonics and Poisson kernels fo...  
3  A finite element approximation for the stochas...  
4  Comparative study of Discrete Wavelet Transfor...

In [ ]:
test_df.tail()

ID                                              TITLE  \
5238  5239  DNN Filter Bank Cepstral Coefficients for Spoo...   
5239  5240  The existence of positive least energy solutio...   
5240  5241  Up-down colorings of virtual-link diagrams and...   
5241  5242  Comparison of SMT and RBMT; The Requirement of...   
5242  5243  Introduction to the Special Issue on Approache...   

                                               ABSTRACT  Computer Science  \
5238    With the development of speech synthesis tec...                 1   
5239    The present study is concerned with the foll...                 0   
5240    We introduce an up-down coloring of a virtua...                 0   
5241    We present in this paper our work on compari...                 1   
5242    The emerging field at the intersection of qu...                 1   

      Physics  Mathematics  Statistics  Quantitative Biology  \
5238        0            0           0                     0   
5239        0            1           0                     0   
5240        0            1           0                     0   
5241        0            0           0                     0   
5242        0            0           0                     1   

      Quantitative Finance  UnrelevantText  
5238                     0               0  
5239                     0               0  
5240                     0               0  
5241                     0               0  
5242                     0               0

In [ ]:
target_list = ['Computer Science', 'Physics', 'Mathematics', 'Statistics', 'Quantitative Biology', 'Quantitative Finance', 'UnrelevantText']
#target_list = ['Частный', 'Государственный', 'Муниципальный', 'Смешанный', 'Стартап', 'Малый', 'Средний', 'Крупный','Локальный', 'Региональный', 'Международный','Физ.Лица', 'Юр.Лица', 'UnrelevantText']
#exclusive_categories1 = ["Стартап", "Малый", "Средний", "Крупный"]
#exclusive_categories2 = ["Частный", "Государственный", "Муниципальный", "Смешанный"]
#exclusive_categories3 = ["Физ.Лица", "Юр.Лица"]
#exclusive_categories4 = ["Локальный", "Национальный", "Международный"]
#another_categories = ['Частный', 'Государственный', 'Муниципальный', 'Смешанный', 'Стартап', 'Малый', 'Средний', 'Крупный','Локальный', 'Региональный', 'Международный','Физ.Лица', 'Юр.Лица', 'UnrelevantText']


# BERT PARAMETERS

In [ ]:
# hyperparameters
MAX_LEN = 128
TRAIN_BATCH_SIZE = 64
VALID_BATCH_SIZE = 64
EPOCHS = 100
LEARNING_RATE = 1e-5
THRESHOLD = 0.5
#threshold (порог) в данном контексте — это значение, которое используется для определения, когда предсказание для категории output_others (например, “UnrelevantText”) становится достаточно уверенным, чтобы оно превалировало над всеми остальными предсказаниями

# BERT MODEL

In [ ]:
from transformers import BertTokenizer, BertModel

In [ ]:
tokenizer = BertTokenizer.from_pretrained('cointegrated/rubert-tiny')
#ignore letter case

In [ ]:
class CustomDataset(torch.utils.data.Dataset):
    def __init__(self, df, tokenizer, max_len):
        self.tokenizer = tokenizer
        self.df = df
        self.title = df['CONTEXT']
        self.targets = self.df[target_list].values
        self.max_len = max_len

    def __len__(self):
        return len(self.title)

    def __getitem__(self, index):
        title = str(self.title[index])
        title = " ".join(title.split())

        inputs = self.tokenizer.encode_plus(
            title,
            None,
            add_special_tokens=True,
            max_length=self.max_len,
            padding='max_length',
            return_token_type_ids=True,
            truncation=True,
            return_attention_mask=True,
            return_tensors='pt'
        )

        return {
            'input_ids': inputs['input_ids'].flatten(),
            'attention_mask': inputs['attention_mask'].flatten(),
            'token_type_ids': inputs["token_type_ids"].flatten(),
            'targets': torch.FloatTensor(self.targets[index])
        }

class TokenizedArticle(CustomDataset):
    def __init__(self, tokenizer, header, body):
        self.tokenizer = tokenizer
        self.header = header
        self.body = body
    def __len__(self):
        super().__len__(self.title)
    def __getitem__(self, index):
        super().__getitem__(index)

        inputs = self.tokenizer.encode_plus(
          title,
          None,
          add_special_tokens=True,
          max_length=self.max_len,
          padding='max_length',
          return_token_type_ids=True,
          truncation=True,
          return_attention_mask=True,
          return_tensors='pt'
        )

        return {
            'input_ids': inputs['input_ids'].flatten(),
            'attention_mask': inputs['attention_mask'].flatten(),
            'token_type_ids': inputs["token_type_ids"].flatten(),
        }

In [ ]:
train_size = 0.5
tmp_dv = train_df.copy()
train_df = tmp_dv.sample(frac=train_size, random_state=200).reset_index(drop=True)
val_df = tmp_dv.drop(train_df.index).reset_index(drop=True)

In [ ]:
val_df.tail()

Computer Science  Physics  Mathematics  Statistics  \
2616                 0        1            0           0   
2617                 0        1            0           0   
2618                 1        0            0           0   
2619                 1        0            0           0   
2620                 0        0            0           0   

      Quantitative Biology  Quantitative Finance  UnrelevantText  \
2616                     0                     0               0   
2617                     0                     0               0   
2618                     0                     0               0   
2619                     0                     0               0   
2620                     1                     0               0   

                                                CONTEXT  
2616  Time-of-Flight Electron Energy Loss Spectrosco...  
2617  Fault Tolerance of Random Graphs with respect ...  
2618  Hybrid CTC-Attention based End-to-End Speech R...  
2619  Model and Integrate Medical Resource Availabil...  
2620  A Deep Learning Approach with an Attention Mec...

In [ ]:
train_dataset = CustomDataset(train_df, tokenizer, MAX_LEN)
valid_dataset = CustomDataset(val_df, tokenizer, MAX_LEN)

In [ ]:
train_data_loader = torch.utils.data.DataLoader(train_dataset,
    batch_size=TRAIN_BATCH_SIZE,
    shuffle=True,
    num_workers=0
)

val_data_loader = torch.utils.data.DataLoader(valid_dataset,
    batch_size=VALID_BATCH_SIZE,
    shuffle=True,
    num_workers=0
)

In [ ]:
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

In [ ]:
device

device(type='cpu')

In [ ]:
def load_ckp(checkpoint_fpath, model, optimizer):
    """
    checkpoint_path: path to save checkpoint
    model: model that we want to load checkpoint parameters into
    optimizer: optimizer we defined in previous training
    """
    # load check point
    checkpoint = torch.load(checkpoint_fpath)
    # initialize state_dict from checkpoint to model
    model.load_state_dict(checkpoint['state_dict'])
    # initialize optimizer from checkpoint to optimizer
    optimizer.load_state_dict(checkpoint['optimizer'])
    # initialize valid_loss_min from checkpoint to valid_loss_min
    valid_loss_min = checkpoint['valid_loss_min']
    # return model, optimizer, epoch value, min validation loss
    return model, optimizer, checkpoint['epoch'], valid_loss_min.item()

def save_ckp(state, is_best, checkpoint_path, best_model_path):
    """
    state: checkpoint we want to save
    is_best: is this the best checkpoint; min validation loss
    checkpoint_path: path to save checkpoint
    best_model_path: path to save best model
    """
    f_path = checkpoint_path
    # save checkpoint data to the path given, checkpoint_path
    torch.save(state, f_path)
    # if it is a best model, min validation loss
    if is_best:
        best_fpath = best_model_path
        # copy that checkpoint file to best path given, best_model_path
        shutil.copyfile(f_path, best_fpath)

In [ ]:
class BERTClass(torch.nn.Module):
    def __init__(self, isTraining, tokenizer, threshold):
        super(BERTClass, self).__init__()
        self.bert_model = BertModel.from_pretrained('cointegrated/rubert-tiny', return_dict=True)
        self.dropout = torch.nn.Dropout(0.4)
        self.isTraining = isTraining
        self.choosentokenizer = tokenizer
        self.threshold = threshold

        """
        # Линейные слои для каждой группы взаимоисключающих категорий
        self.fc_exclusive1 = torch.nn.Linear(312, 4)  # "Стартап", "Малый", "Средний", "Крупный"
        self.fc_exclusive2 = torch.nn.Linear(312, 4)  # "Частный", "Государственный"
        self.fc_exclusive3 = torch.nn.Linear(312, 2)  # "Физ.Лица", "Юр.Лица"
        self.fc_exclusive4 = torch.nn.Linear(312, 3)  # "Локальный", "Региональный", "Международный"
        """

        # Линейный слой для оставшихся независимых категорий
        self.fc_others = torch.nn.Linear(312, 7)  # "UnrelevantText"

        # Линейный слой для определения релевантности текста
        self.fc_relevance = torch.nn.Linear(312, 2)  # "Релевантный" или "Нерелевантный"

    def forward(self, input_ids, attn_mask, token_type_ids):
        # Выход BERT модели
        output = self.bert_model(
            input_ids,
            attention_mask=attn_mask,
            token_type_ids=token_type_ids
        )
        pooled_output = self.dropout(output.pooler_output)

        """
        # Взаимоисключающие категории
        output_exclusive1 = torch.softmax(self.fc_exclusive1(pooled_output), dim=1)
        output_exclusive2 = torch.softmax(self.fc_exclusive2(pooled_output), dim=1)
        output_exclusive3 = torch.softmax(self.fc_exclusive3(pooled_output), dim=1)
        output_exclusive4 = torch.softmax(self.fc_exclusive4(pooled_output), dim=1)
        """

        # Применение порога 0.5 к вероятностям
        """
        if not self.isTraining:
          output_exclusive1 = torch.where(output_exclusive1.max(dim=1, keepdim=True).values > self.threshold, output_exclusive1, torch.zeros_like(output_exclusive1))
          output_exclusive2 = torch.where(output_exclusive2.max(dim=1, keepdim=True).values > self.threshold, output_exclusive2, torch.zeros_like(output_exclusive2))
          output_exclusive3 = torch.where(output_exclusive3.max(dim=1, keepdim=True).values > self.threshold, output_exclusive3, torch.zeros_like(output_exclusive3))
          output_exclusive4 = torch.where(output_exclusive4.max(dim=1, keepdim=True).values > self.threshold, output_exclusive4, torch.zeros_like(output_exclusive4))
        """

        # Остальные категории
        output_others = torch.sigmoid(self.fc_others(pooled_output))

        # Релевантность текста
        relevance_logits = self.fc_relevance(pooled_output)  # [batch_size, 2]
        relevance_output = torch.softmax(relevance_logits, dim=1)  # Вероятности релевантности

        # Конкатенация всех предсказаний в один тензор
        final_output = torch.cat([
            #output_exclusive1,  # 4 logits
            #output_exclusive2,  # 4 logits
            #output_exclusive3,  # 2 logits
            #output_exclusive4,  # 3 logits
            output_others       # 1 logit
        ], dim=1)  # Объединяем по последней размерности

        # Бинарный выход: 1, если текст релевантный, иначе 0
        binary_output = torch.argmax(relevance_output, dim=1).float()  # [batch_size]

        return {
            "final_output": final_output,    # Все предсказания
            "binary_output": binary_output,  # Бинарное решение
            "relevance_output": relevance_output,  # Вероятности релевантности
            #"ou1": output_exclusive1,
            #"ou2": output_exclusive2,
            #"ou3": output_exclusive3,
            #"ou4": output_exclusive4,
            "oo": output_others
        }
    def save_weights(self, file_path):
        """
        Сохраняет веса модели в текстовый файл.
        """
        with open(file_path, 'w') as f:
            for layer_name, weight_tensor in self.state_dict().items():
                f.write(f"Layer: {layer_name}\n")
                f.write(f"Shape: {list(weight_tensor.shape)}\n")
                f.write(f"Weights: {weight_tensor.numpy().tolist()}\n")
                f.write("\n")  # Разделитель между слоями
        print(f"Weights saved to {file_path}")

    def load_weights(self, file_path):
        """
        Загружает веса модели из текстового файла.
        """
        import ast  # Для преобразования строки в Python-объект
        state_dict = self.state_dict()
        with open(file_path, 'r') as f:
            lines = f.readlines()

    def save_weights_in_parts(self, folder_path):
        """
        Сохраняет веса модели по частям
        """
        os.makedirs(folder_path, exist_ok=True)

        state_dict = self.state_dict()
        # Сохраняем каждый ключ отдельно
        for key in state_dict:
            part_path = os.path.join(folder_path, f"{key}.pt")
            torch.save({key: state_dict[key]}, part_path)
            print(f"Сохранена часть {key} в файл {part_path}")

    def load_weights_in_parts(self, folder_path):
      """
      Загружает веса модели из всех файлов в указанной папке
      """
      """
      state_dict = {}

      # Перебираем файлы в указанной директории
      for part_file in os.listdir(folder_path):
          part_path = os.path.join(folder_path, part_file)

          # Проверяем, что это файл и он заканчивается на .pt
          if os.path.isfile(part_path) and part_file.endswith(".pt"):
              part = torch.load(part_path)
              state_dict.update(part)
              print(f"Загружена часть из файла {part_path}")
          else:
              print(f"Пропущен файл {part_path}, так как это не .pt файл или это директория.")

      # Загружаем объединенное состояние в модель
      model.load_state_dict(state_dict)
      print("Все части объединены и загружены в модель."
      """
      # Проверяем, что указанная папка существует
      if not os.path.isdir(folder_path):
          raise ValueError(f"Указанный путь {folder_path} не является директорией.")

      # Получаем список файлов .pt
      weight_files = [
          os.path.join(folder_path, file)
          for file in os.listdir(folder_path)
          if os.path.isfile(os.path.join(folder_path, file)) and file.endswith(".pt")
      ]

      if not weight_files:
          raise ValueError(f"В директории {folder_path} не найдено файлов с расширением .pt.")

      # Загружаем веса из каждого файла
      for file_path in weight_files:
          try:
              print(f"Загружается файл весов: {file_path}")
              weights = torch.load(file_path)
              self.load_state_dict(weights, strict=False)  # strict=False, чтобы избежать ошибок несовпадения
              print(f"Файл {file_path} успешно загружен.")
          except Exception as e:
              print(f"Ошибка при загрузке файла {file_path}: {e}")

      print("Все файлы в папке успешно обработаны.")

    def validate_article(self, header, body):
      tokenized_article = self.choosentokenizer(header, body, padding='max_length', truncation=True, return_tensors='pt')
      results = self.forward(tokenized_article['input_ids'], tokenized_article['attention_mask'], tokenized_article['token_type_ids'])
      return results

    def analyze(self, header, body):
      resultsOfValidation = self.validate_article(header, body)
      if resultsOfValidation["binary_output"] == 0:
        return "UnrelevantText"
      else:
        tags = []
        bool_mask = resultsOfValidation["oo"] > 0.5

        indices = torch.nonzero(bool_mask)

        # Преобразуем индексы в одномерный список
        tags = [another_categories[idx[1].item()] for idx in indices if idx[1].item() != 13]
        #print(indices)
        """
        # Используем torch.argmax для нахождения индекса максимального значения
        if torch.sum(resultsOfValidation["ou1"]) > 0:
            max_idx = torch.argmax(resultsOfValidation["ou1"]).item()
            tags.append(exclusive_categories1[max_idx])

        if torch.sum(resultsOfValidation["ou2"]) > 0:
            max_idx = torch.argmax(resultsOfValidation["ou2"]).item()
            tags.append(exclusive_categories2[max_idx])

        if torch.sum(resultsOfValidation["ou3"]) > 0:
            max_idx = torch.argmax(resultsOfValidation["ou3"]).item()
            tags.append(exclusive_categories3[max_idx])

        if torch.sum(resultsOfValidation["ou4"]) > 0:
            max_idx = torch.argmax(resultsOfValidation["ou4"]).item()
            tags.append(exclusive_categories4[max_idx])
        """
      return tags


model = BERTClass(False, tokenizer, THRESHOLD)
#model.to(device)


In [ ]:
def loss_fn(outputs, targets):
    return torch.nn.BCEWithLogitsLoss()(outputs, targets)

optimizer = torch.optim.Adam(params =  model.parameters(), lr=LEARNING_RATE)

In [ ]:
val_targets=[]
val_outputs=[]

In [ ]:
def train_model(n_epochs, training_loader, validation_loader, model,
                optimizer, checkpoint_path, best_model_path):

  train_losses = []
  valid_losses = []

  # initialize tracker for minimum validation loss
  valid_loss_min = np.Inf


  for epoch in range(1, n_epochs+1):
    train_loss = 0
    valid_loss = 0

    model.train()
    print('===Epoch {}: Training Start==='.format(epoch))
    for batch_idx, data in enumerate(training_loader):
        #print('yyy epoch', batch_idx)
        ids = data['input_ids'].to(device, dtype = torch.long)
        mask = data['attention_mask'].to(device, dtype = torch.long)
        token_type_ids = data['token_type_ids'].to(device, dtype = torch.long)
        targets = data['targets'].to(device, dtype = torch.float)

        results = model(ids, mask, token_type_ids)
        outputs = results["final_output"]
        IsActual = results["binary_output"]

        optimizer.zero_grad()
        loss = loss_fn(outputs, targets)
        #if batch_idx%5000==0:
         #   print(f'Epoch: {epoch}, Training Loss:  {loss.item()}')

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        print('before loss data in training', loss.item(), train_loss)
        train_loss = train_loss + ((1 / (batch_idx + 1)) * (loss.item() - train_loss))
        print('after loss data in training', loss.item(), train_loss)
    print('===Epoch {}: Training End==='.format(epoch))

    print('===Epoch {}: Validation Start==='.format(epoch))
    ######################
    # validate the model #
    ######################

    model.eval()

    with torch.no_grad():
      for batch_idx, data in enumerate(validation_loader):
            ids = data['input_ids'].to(device, dtype = torch.long)
            mask = data['attention_mask'].to(device, dtype = torch.long)
            token_type_ids = data['token_type_ids'].to(device, dtype = torch.long)
            targets = data['targets'].to(device, dtype = torch.float)
            #=====
            ProbabilityOutputs = model(ids, mask, token_type_ids)["final_output"]
            IsNotActualArticle = model(ids, mask, token_type_ids)["binary_output"]
            outputs = torch.cat([ProbabilityOutputs], dim=1)
            #=====
            #print(outputs)

            loss = loss_fn(outputs, targets)
            valid_loss = valid_loss + ((1 / (batch_idx + 1)) * (loss.item() - valid_loss))
            val_targets.extend(targets.cpu().detach().numpy().tolist())
            val_outputs.extend(torch.sigmoid(outputs).cpu().detach().numpy().tolist())
            print(val_outputs)

      print('===Epoch {}: Validation End==='.format(epoch))

      train_loss = train_loss / len(training_loader)
      valid_loss = valid_loss / len(validation_loader)
      train_losses.append(train_loss)
      valid_losses.append(valid_loss)

      # calculate average losses
      #print('before cal avg train loss', train_loss)
      #print(len(training_loader))
      train_loss = train_loss/len(training_loader)
      #print(len(validation_loader))
      valid_loss = valid_loss/len(validation_loader)
      # print training/validation statistics
      #print(model(ids, mask, token_type_ids)["relevance_output"])
      #print(model(ids, mask, token_type_ids)["binary_output"])
      print('Epoch: {} \tAvgerage Training Loss: {:.6f} \tAverage Validation Loss: {:.6f}'.format(
            epoch,
            train_loss,
            valid_loss
            ))
      # create checkpoint variable and add important data
      checkpoint = {
            'epoch': epoch + 1,
            'valid_loss_min': valid_loss,
            'state_dict': model.state_dict(),
            'optimizer': optimizer.state_dict()
      }

        # save checkpoint
      save_ckp(checkpoint, False, checkpoint_path, best_model_path)

      ## TODO: save the model if validation loss has decreased
      if valid_loss <= valid_loss_min:
        print('Validation loss decreased ({:.6f} --> {:.6f}).  Saving model ...'.format(valid_loss_min,valid_loss))
        # save checkpoint as best model
        save_ckp(checkpoint, True, checkpoint_path, best_model_path)
        valid_loss_min = valid_loss

    print('===Epoch {}  Done===\n'.format(epoch))

  return model, train_losses, valid_losses


In [ ]:
ckpt_path = "/content/drive/MyDrive/datasets/multi-label/curr_ckpt"
best_model_path = "/content/drive/MyDrive/datasets/multi-label/best_model.pt"

In [ ]:
#model.load_weights_in_parts(save_dir)

In [ ]:
trained_model, train_losses, valid_losses = train_model(
    EPOCHS, train_data_loader, val_data_loader, model, optimizer, ckpt_path, best_model_path
)

===Epoch 1: Training Start===
before loss data in training 0.8935295939445496 0
after loss data in training 0.8935295939445496 0.8935295939445496
before loss data in training 0.887167751789093 0.8935295939445496
after loss data in training 0.887167751789093 0.8903486728668213
before loss data in training 0.8862056732177734 0.8903486728668213
after loss data in training 0.8862056732177734 0.8889676729838053
before loss data in training 0.8868752121925354 0.8889676729838053
after loss data in training 0.8868752121925354 0.8884445577859879
before loss data in training 0.8744688034057617 0.8884445577859879
after loss data in training 0.8744688034057617 0.8856494069099426
before loss data in training 0.8820968866348267 0.8856494069099426
after loss data in training 0.8820968866348267 0.8850573201974233
before loss data in training 0.8798586130142212 0.8850573201974233
after loss data in training 0.8798586130142212 0.8843146477426802
before loss data in training 0.8870951533317566 0.88431464

KeyboardInterrupt: 

In [ ]:
trained_model.save_weights_in_parts(save_dir)

In [ ]:
#trained_model.load_weights_in_parts(save_dir)

In [ ]:
print("Текущие веса:")
for name, param in model.named_parameters():
    print(f"{name}: {param.sum()}")

In [ ]:
print("Загруженные веса:")
for name, param in model.named_parameters():
    print(f"{name}: {param.sum()}")

In [ ]:
test_article = "Правительственные меры по поддержке малого и среднего бизнеса в России"
test_text = "Для малого и среднего бизнеса предусмотрены различные меры поддержки, включая налоговые льготы и субсидии на развитие и инновации."
results = trained_model.analyze(test_article, test_text)
print(results)
print("===")
test_article = "Государственные программы для крупного сельскохозяйственного бизнеса"
test_text = "Программы субсидирования для крупных фермерских хозяйств направлены на повышение устойчивости и конкурентоспособности в аграрной сфере."
results = trained_model.analyze(test_article, test_text)
print(results)
print("===")
test_article = "Изучаем культуру японской кухни: интересные факты и рецепты"
test_text = "Изучение японской кухни и приготовление традиционных блюд. История и развитие японской гастрономической культуры."
results = trained_model.analyze(test_article, test_text)
print(results)

In [ ]:
for index, row in test_df.iterrows():
  results = trained_model.analyze(row['TITLE'], row['ABSTRACT'])
  print(row['TITLE'], row['ABSTRACT'])
  print(results)

In [ ]:
# Проверим, что данные не пустые
print(f"Train losses: {train_losses}")
print(f"Validation losses: {valid_losses}")

# Построение графиков
plt.figure(figsize=(12, 6))

# График потерь
plt.subplot(1, 2, 1)
plt.plot(range(1, EPOCHS + 1), train_losses, label='Training Loss', color='blue')
plt.plot(range(1, EPOCHS + 1), valid_losses, label='Validation Loss', color='red')
plt.xlabel('Epoch')
plt.ylabel('Loss')
plt.legend()
plt.title('Training and Validation Loss')

# Отображаем графики
plt.tight_layout()
plt.show()